In [17]:
import data_loader
from data_loader import load_meshes
import importlib
importlib.reload(data_loader)
from transforms import SDF_transform, rotate, round_to_interval, flatten_index
from pysdf import SDF  
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix
from sklearn.metrics import ConfusionMatrixDisplay 
from matplotlib import pyplot as plt
from mpl_toolkits.mplot3d import Axes3D


In [93]:
final_list = ['D:/Projects/Shadow Art/data/sparse\\armchair.obj',
                  'D:/Projects/Shadow Art/data/sparse\\0c78aaf693f44865a06384e0c6a21103.glb',
                  'D:/Projects/Shadow Art/data/sparse\\teapot.obj',
                  'D:/Projects/Shadow Art/data/sparse\\torus.obj',
                  'D:/Projects/Shadow Art/data/sparse\\toy.glb',
                  'D:/Projects/Shadow Art/data/sparse\\flyhead.glb',
                  'D:/Projects/Shadow Art/data/sparse\\shark.glb',
                  'D:/Projects/Shadow Art/data/sparse\\pot.glb',
                  'D:/Projects/Shadow Art/data/sparse\\portal.glb',
                  'D:/Projects/Shadow Art/data/sparse\\axe.glb'
                  ]
obj_list  = load_meshes(final_list, normalize=True,target_range=(30,70))

In [94]:
# grid
size = np.linspace(0, 99, 100)
x, y, z = np.meshgrid(size, size, size)
grid = np.column_stack((x.flatten(), y.flatten(), z.flatten()))
grid = grid.astype(np.int32)
grid

array([[ 0,  0,  0],
       [ 0,  0,  1],
       [ 0,  0,  2],
       ...,
       [99, 99, 97],
       [99, 99, 98],
       [99, 99, 99]])

In [95]:
obj_list[0].vertices.min()

30.0

In [96]:
sdf_list = []
for obj in obj_list:
    sdf_list.append(SDF(obj.vertices, obj.faces))

sdf_list

[<sdf.SDF(verts.shape=(3988, 3), faces.shape=(5588, 3), robust=True)>,
 <sdf.SDF(verts.shape=(4914, 3), faces.shape=(2800, 3), robust=True)>,
 <sdf.SDF(verts.shape=(3484, 3), faces.shape=(6320, 3), robust=True)>,
 <sdf.SDF(verts.shape=(2304, 3), faces.shape=(1152, 3), robust=True)>,
 <sdf.SDF(verts.shape=(267, 3), faces.shape=(436, 3), robust=True)>,
 <sdf.SDF(verts.shape=(448, 3), faces.shape=(224, 3), robust=True)>,
 <sdf.SDF(verts.shape=(1293, 3), faces.shape=(1490, 3), robust=True)>,
 <sdf.SDF(verts.shape=(6096, 3), faces.shape=(10000, 3), robust=True)>,
 <sdf.SDF(verts.shape=(234, 3), faces.shape=(220, 3), robust=True)>,
 <sdf.SDF(verts.shape=(96, 3), faces.shape=(188, 3), robust=True)>]

In [111]:
import random
def random_translate(num_points, lower_bound, upper_bound):
    points = []
    mean = (lower_bound + upper_bound) / 2  # Mean is the midpoint of the range
    std_dev = (upper_bound - lower_bound) / 6
    for _ in range(num_points): 
        x = np.clip(np.random.normal(mean, std_dev), lower_bound, upper_bound)
        y = np.clip(np.random.normal(mean, std_dev), lower_bound, upper_bound)
        z = np.clip(np.random.normal(mean, std_dev), lower_bound, upper_bound)
        points.append((x, y, z))
    return points

def random_rotate(num_points, lower_bound, upper_bound):
    points = []
    mean = (lower_bound + upper_bound) / 2  # Mean is the midpoint of the range
    std_dev = (upper_bound - lower_bound) / 6
    for _ in range(num_points): 
        x = np.clip(np.random.normal(mean, std_dev), lower_bound, upper_bound)
        y = np.clip(np.random.normal(mean, std_dev), lower_bound, upper_bound)
        z = np.clip(np.random.normal(mean, std_dev), lower_bound, upper_bound)
        points.append((x, y, z))
    return points

In [112]:
from visualization import create_mesh, combine_meshes, join_meshes_as_scene, show_scene

mesh_list = [create_mesh(o.vertices + random_translate(1, -100, 100), o.faces) for o in obj_list]
# mesh_list = [create_mesh(o.vertices, o.faces) for o in obj_list]
show_scene(combine_meshes(mesh_list))

In [99]:
contains_mask_list = []
for sdfs in sdf_list:
    contains_mask_list.append(sdfs.contains(grid))

np.count_nonzero(contains_mask_list[0])

30845

### transform mask and get the sdf

In [100]:
R = [np.pi/8, np.pi/12, np.pi/10]
# R = [0,0,0]
# T = [1, -1, 1]
T = [10, -10 ,10 ]

d = grid[1][2] -  grid[0][0]
k = int(np.cbrt(len(grid)))
a = grid[0][0]
b = grid[-1][0] + d

In [101]:
transformed_sdf_list = SDF_transform(contains_mask_list,R, T, grid)
transformed_sdf_list

array([[False, False, False, ..., False, False, False],
       [False, False, False, ..., False, False, False],
       [False, False, False, ..., False, False, False],
       ...,
       [False, False, False, ..., False, False, False],
       [False, False, False, ..., False, False, False],
       [False, False, False, ..., False, False, False]])

### transform object points, compute the sdf again


In [102]:
new_vertices_list = []
for obj in obj_list:
    new_vertices = obj.vertices
    new_vertices = rotate(new_vertices, R)
    new_vertices = new_vertices + T 
    # new_vertices = round_to_interval(new_vertices, a, b, k)
    new_vertices_list.append(new_vertices)

new_sdf_list = []
for i,obj in enumerate(obj_list):
    new_sdf_list.append(SDF(new_vertices_list[i], obj.faces))

new_contains_mask_list = []
for sdfs in new_sdf_list:
    new_contains_mask_list.append(sdfs.contains(grid))

In [103]:
np.sum(transformed_sdf_list[0])

26761

In [104]:
np.sum(new_contains_mask_list[0])

32600

In [109]:
from visualization import scatter_plot
scatter_plot(transformed_sdf_list[0], grid)

### results

In [ ]:
for obj in obj_list:
    T = random_translate(1, -20, 20)